#### Importing Bokeh

In [ ]:
from bokeh.io import push_notebook, show, output_notebook
from bokeh.plotting import figure

from bokeh.models import ColumnDataSource
output_notebook()

#### A simple example
Lets assume we want to create interactive plots that could be updated any time. We can do this in Bokeh by storing data in a `ColumnDataSource` and calling `push_notebook()` every time we update the data. Here is how it works:

In [ ]:
# creating a Figure object 
fig = figure(title='Interactive plots')
source = ColumnDataSource(dict(x=[1,2,3,4], y=[3,6,4,8]))
fig.line('x', 'y', source=source)
handle = show(fig, notebook_handle=True)

Now we update the data:

In [ ]:
source.data.update({
    'y': [10,4,7,1]
})

push_notebook(handle)

It works! But what if we wanted to create plots on the go, meaning adding new plots after calling `show(fig,..)`. For instance, say we want to visualize a number of AV trajectories but we don't know how many, and we want to add trajectories to our figure as we go. We also want to be able to update those trajectories continually. Lets start by adding another graph to our existing figure.

In [ ]:
# this one has a different data source
another_source = ColumnDataSource(dict(a=[1,2,3,4,5], b=[3,4,5,4,3]))
fig.line('a','b',source=another_source, color='red')
push_notebook(handle)

Great, we can add new plots to the existing figure with no hassle. Now lets see if we could update this graph the same as before.

In [ ]:
another_source.data.update({
    'b': [10,8,6,8,10]
})

push_notebook(handle)

As you can see the graph doesn't get updated even though we updated the datasource. This is a problem in current version of Bokeh. Currently, the dynamic updating of the graph only works for the datasources created before calling the function `show()`.

### ColumnDataSourcePool
In order to circumvent the issue mentioned before, and to ease the use of datasources for plotting multiple graphs, we implemented a new data structure called `ColumnDataSourcePool`. It reserves a pool of `ColumnDataSource` objects available on demand, all of which are registered with one or more figure. The sources are assumed to be ready to use via unique keys. That means the allocation mechanism is concealed from the user and the pool could be used like a dictionary to access any source identified by a unique key.

In [ ]:
from vis.jupyter_notebooks.plotters import ColumnDataSourcePool

In [ ]:
fig = figure(title='Mutlple plots on the go')
source_pool = ColumnDataSourcePool(cap=20)  # Maximum number of available sources is 20
source_pool.register_figure(fig)

handle = show(fig, notebook_handle=True)
source_pool.dump(handle)

Notice we dont add any graph at the beginning. So the figure is empty.

In [ ]:
source_pool['first'].data = dict(x=[1,2,3],y=[4,5,6])
fig.line('x','y', source=source_pool['first'], color='red')
push_notebook(handle)

In [ ]:
source_pool['second'].data = dict(x=[1,2,3],y=[4,5,6])
fig.scatter('x','y', source=source_pool['second'], color='blue', radius=0.025)
push_notebook(handle)

In [ ]:
source_pool['another'].data = dict(x=[],y=[]) # leaving this one empty to appear later
fig.line('x','y', source=source_pool['another'], color='green')
push_notebook(handle)

Now let's update these sources to see if that would update the graphs.

In [ ]:
source_pool['first'].data.update({'y': [6,5,4]})
source_pool['second'].data.update({'y': [5,5,4]})
source_pool['another'].data.update({'x':[1.5,1.5,2.5,2.5], 'y': [3,6,6,3]})
push_notebook(handle)

And now we clear all the data from all the sources..

In [ ]:
source_pool.flush()
push_notebook(handle)

It works!! You can see using this data structure we can dynamically add graphs and update them. 
The datastructure also features syncing behavior between the datasource. It could be setup to synchronizet the selection, hover, and tapping behavior between the sources in the pool. 